# MAIN NOTEBOOK 

### This notebook imports the required python scripts and compute all required work

### This notebook has been used on google colab following the order provided

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:

!git clone https://github.com/alialhousseini/glimpse-mds

Cloning into 'glimpse-mds'...
remote: Enumerating objects: 533, done.
remote: Counting objects: 100% (93/93), done.
remote: Compressing objects: 100% (73/73), done.
remote: Total 533 (delta 48), reused 51 (delta 20), pack-reused 440 (from 1)
Receiving objects: 100% (533/533), 48.63 MiB | 17.78 MiB/s, done.
Resolving deltas: 100% (310/310), done.


________

#### Functions used to generated GSpeaker and GUnique Results

In [ ]:
def consensus_scores_based_summaries(sample, n_consensus=3, n_dissensus=3):
    consensus_samples = sample['consensuality_scores'].sort_values(ascending=True).head(n_consensus).index.tolist()
    disensus_samples = sample['consensuality_scores'].sort_values(ascending=False).head(n_dissensus).index.tolist()

    consensus = ".".join(consensus_samples)
    disensus = ".".join(disensus_samples)

    return consensus + "\n\n" + disensus


def rsa_scores_based_summaries(sample, n_consensus=3, n_rsa_speaker=3):
    consensus_samples = sample['consensuality_scores'].sort_values(ascending=True).head(n_consensus).index.tolist()
    rsa = sample['best_rsa'].tolist()[:n_rsa_speaker]

    consensus = ".".join(consensus_samples)
    rsa = ".".join(rsa)

    return consensus + "\n\n" + rsa

In [ ]:

%cd glimpse-mds/

/content/glimpse-mds


Now path is fixed

In [ ]:
#Testing
from pathlib import Path
test = Path('data/all_reviews_2017.csv')
test.is_file()

True

Installing & Importing all necessary libraries

In [ ]:
%%capture
!pip install pandas
!pip install torch
!pip install datasets
!pip install tqdm
!pip install transformers
!pip install nltk
!pip install pickle
!pip install numpy
!pip install operator

In [ ]:
import pandas as pd
from torch.utils.data import DataLoader
from datasets import Dataset
from tqdm import tqdm
import datetime
import torch
from pathlib import Path
from transformers import AutoModelForSeq2SeqLM, AutoTokenizer, AutoModelForCausalLM
import torch
from typing import List, Dict
import nltk
import pickle
import re
import numpy as np
from functools import reduce
import operator
import random
import json
import os
nltk.download('punkt')
nltk.download('punkt_tab')

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
[nltk_data] Downloading package punkt_tab to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt_tab.zip.


True

Fix a seed 

In [ ]:
def set_random_seed(seed: int):
    random.seed(seed)  # For Python's random
    np.random.seed(seed)  # For NumPy
    torch.manual_seed(seed)  # For PyTorch on CPU
    torch.cuda.manual_seed(seed)  # For PyTorch on GPU


set_random_seed(42)

Summary Generator 

- Accepts a set of models, and a set of datasets
- For each dataset it generates 
    - Extractive summary
    - Abstractive summary using each of the models provided
- *Note*: It ensures to clean inputs before processing

In [ ]:

class SummaryGenerator:

    model = AutoModelForSeq2SeqLM.from_pretrained("facebook/bart-large-cnn")
    tokenizer = AutoTokenizer.from_pretrained("facebook/bart-large-cnn")

    def __init__(self, model_name: str = 'BART', model=model, tokenizer=tokenizer, device="cuda"):
        self.model_name = model_name
        self.model = model
        self.tokenizer = tokenizer
        self.device = device
        self.generation_config = {
            "max_new_tokens": 200,
            "do_sample": True,
            "top_p": 0.95,
            "temperature": 1.0,
            "num_return_sequences": 8,
            "num_beams": 1,
            "early_stopping": True,
            "min_length": 0,
        }

    def evaluate_summarizer(self, dataset_path: Path, batch_size: int, trimming: bool, checkpoint_path: str) -> Dataset:
        """
        @param model: The model used to generate the summaries
        @param tokenizer: The tokenizer used to tokenize the text and the summary
        @param dataset: A dataset with the text
        @param decoding_config: Dictionary with the decoding config
        @param batch_size: The batch size used to generate the summaries
        @return: The same dataset with the summaries added
        """
        try:
            dataset = pd.read_csv(dataset_path)
        except:
            raise ValueError(f"Unknown dataset {dataset_path}")

        # make a dataset from the dataframe
        dataset = Dataset.from_pandas(dataset)

        # create a dataloader
        dataloader = DataLoader(
            dataset, batch_size=batch_size, shuffle=False, drop_last=trimming)

        # Checkpoint file to save progress
        if os.path.exists(checkpoint_path):
            with open(checkpoint_path, "r") as f:
                checkpoint = json.load(f)
        else:
            checkpoint = {"processed_batches": 0, "summaries": []}

        summaries = checkpoint["summaries"]
        print("Generating summaries...")

        self.model.to(self.device)

        for batch_idx, batch in enumerate(tqdm(dataloader)):
            # Skip already processed batches
            if batch_idx < checkpoint["processed_batches"]:
                continue

            text = batch["text"]

            inputs = self.tokenizer(
                text,
                max_length=min(self.tokenizer.model_max_length,
                               768),  # Adjust max_length
                padding="max_length",
                truncation=True,
                return_tensors="pt",
            )

            # move inputs to device
            inputs = {key: value.to(self.device)
                      for key, value in inputs.items()}

            # generate summaries
            try:
                with torch.amp.autocast('cuda'):
                    outputs = self.model.generate(
                        **inputs, **self.generation_config)
            except RuntimeError as e:
                print(f"Error during generation: {e}")
                print(f"Input shape: {inputs['input_ids'].shape}")
                # Save progress before raising an error
                checkpoint["processed_batches"] = batch_idx
                checkpoint["summaries"] = summaries
                with open(checkpoint_path, "w") as f:
                    json.dump(checkpoint, f)
                raise

            total_size = outputs.numel()  # Total number of elements in the tensor
            # Target size of the last dimension
            target_size = batch_size * outputs.shape[-1]
            # Calculate the required padding size to make the total number of elements divisible by the target size
            pad_size = (target_size - (total_size % target_size)) % target_size

            # Pad the tensor with zeros to make the total number of elements divisible by the target size
            if not trimming and pad_size != 0:
                outputs = torch.nn.functional.pad(
                    outputs, (0, 0, 0, pad_size // outputs.shape[-1]))

            # output : (batch_size * num_return_sequences, max_length)
            try:
                outputs = outputs.reshape(batch_size, -1, outputs.shape[-1])
            except Exception as e:
                print(f"Error reshaping outputs: {e}")
                raise ValueError(f"Cannot reshape tensor of size {outputs.numel()} into shape "
                                 f"({batch_size}, -1, {outputs.shape[-1]}).")

            # decode summaries
            for b in range(batch_size):
                summaries.append(
                    [
                        self.tokenizer.decode(
                            outputs[b, i],
                            skip_special_tokens=True,
                        )
                        for i in range(outputs.shape[1])
                    ]
                )

            # Save progress after processing each batch
            checkpoint["processed_batches"] = batch_idx + 1
            checkpoint["summaries"] = summaries
            with open(checkpoint_path, "w") as f:
                json.dump(checkpoint, f)

            # if trimming the last batch, remove them from the dataset
            if trimming:
                dataset = dataset.select(range(len(summaries)))

        # add summaries to the huggingface dataset
        dataset = dataset.map(lambda example: {"summary": summaries.pop(0)})

        # Clean up the checkpoint file after successful completion
        if os.path.exists(checkpoint_path):
            os.remove(checkpoint_path)

        return dataset

    def generate_abstractive_summary(self, dataset_path: Path, batch_size: int, trimming: bool):
        self.tokenizer.pad_token = self.tokenizer.unk_token
        self.tokenizer.pad_token_id = self.tokenizer.unk_token_id

        dataset = self.evaluate_summarizer(
            dataset_path, batch_size, trimming, checkpoint_path="summarizer_checkpoint.json"
        )

        df_dataset = dataset.to_pandas()
        df_dataset = df_dataset.explode('summary')
        df_dataset = df_dataset.reset_index()
        # add an idx with  the id of the summary for each example
        df_dataset['id_candidate'] = df_dataset.groupby(['index']).cumcount()

        output_path = Path(
            f"data/candidates/{self.model_name}_{dataset_path.stem}_-_abstr.csv")
        # create output dir if it doesn't exist
        if not output_path.parent.exists():
            output_path.parent.mkdir(parents=True, exist_ok=True)
        df_dataset.to_csv(output_path, index=False, encoding="utf-8")
        print('done')

    def generate_extractive_summary(self, dataset_path: Path):
        try:
            dataset = pd.read_csv(dataset_path)
        except:
            raise ValueError(f"Unknown dataset {dataset_path}")

        # make a dataset from the dataframe
        dataset = Dataset.from_pandas(dataset)

        summaries = []

        # (tqdm library for progress bar)
        for sample in tqdm(dataset):
            text = sample["text"]

            # Replace any set of successive dashes (e.g., --, ----, -----) with a newline
            text = re.sub(r'-{2,}', '\n', text)

            # Remove patterns like ".2-" or isolated numerics with hyphens
            text = re.sub(r'\.\d+-', '', text)

            # Replace multiple newlines or spaces with a single newline or space
            # Replace multiple newlines with one
            text = re.sub(r'\n+', '\n', text)
            # Replace multiple spaces with one
            text = re.sub(r'\s+', ' ', text)

            # Remove any remaining unwanted characters (e.g., control characters)
            # Remove non-ASCII characters
            text = re.sub(r'[^\x00-\x7F]+', '', text)

            # To be discussed
            text = text.replace("\n", " ")

            sentences = nltk.sent_tokenize(text)

            # remove empty sentences
            sentences = [sentence for sentence in sentences if sentence != ""]

            # Filter out short or meaningless sentences
            sentences = [sent for sent in sentences if len(sent) > 8]

            summaries.append(sentences)

        # add summaries to the huggingface dataset
        dataset = dataset.map(lambda example: {"summary": summaries.pop(0)})

        df_dataset = dataset.to_pandas()
        df_dataset = df_dataset.explode("summary")
        df_dataset = df_dataset.reset_index()
        # add an idx with  the id of the summary for each example
        df_dataset["id_candidate"] = df_dataset.groupby(["index"]).cumcount()

        output_path = f"data/candidates/{dataset_path.stem}_-_extr.csv"
        output_path = Path(output_path)
        # create output dir if it doesn't exist
        if not output_path.parent.exists():
            output_path.parent.mkdir(parents=True, exist_ok=True)
        df_dataset.to_csv(output_path, index=False, encoding="utf-8")
        print('done')

    def change_model(self, model_name, model, tokenizer):
        self.model_name = model_name
        self.model = model
        self.tokenizer = tokenizer
########################################################################

KeyboardInterrupt: 

Running summary generator

In [ ]:
# Iterate over the dataset and generate (extractive) summaries first
path_original_dataset = Path("/content/drive/MyDrive/original_data")

model_for_extractive = {
    'model_1':
        {
            'model_id': "facebook/bart-large-cnn",
            'model_name': "BART"

        },
    'model_2':
        {
            'model_id': "google/pegasus-arxiv",
            'model_name': "PEGASUS-Arxiv"
        },
    'model_3':
        {
            'model_id': "google/pegasus-large",
            'model_name': "PEGASUS-Large"
        },
}

# Load the model and tokenizer
model = AutoModelForSeq2SeqLM.from_pretrained(
    model_for_extractive["model_1"]['model_id'])
tokenizer = AutoTokenizer.from_pretrained(
    model_for_extractive["model_1"]['model_id'])
model_name = model_for_extractive["model_1"]['model_name']

# Initialize the SummaryGenerator
sg = SummaryGenerator()
for model_count, model_info in model_for_extractive.items():
    model_id = model_info['model_id']
    model_name = model_info['model_name']

    # Adjust SG params
    model = AutoModelForSeq2SeqLM.from_pretrained(model_id)
    tokenizer = AutoTokenizer.from_pretrained(model_id)
    sg.change_model(model_name, model, tokenizer)

    # Iterate over the datasets
    for file in path_original_dataset.glob('*.csv'):

        # Generate extractive summaries for this dataset
        sg.generate_abstractive_summary(file, 16, False)

# Once all extractive summaries are generated, generate abstractive summaries
for file in path_original_dataset.glob('*.csv'):
    sg.generate_extractive_summary(file)

# By this we generated all abstractive and extractive summaries for all our datasets
########################################################################
print("GENERATION OF ABS/EXT SUMMARIES DONE")


100%|██████████| 580/580 [00:00<00:00, 1213.15it/s]


Map:   0%|          | 0/580 [00:00<?, ? examples/s]

done
GENERATION OF ABS/EXT SUMMARIES DONE


Instantiating RSA RERANKER


In [ ]:
class RSAReranking:
    """
    Rerank a list of candidates according to the RSA model.
    """

    def __init__(
            self,
            model,
            tokenizer,
            candidates: List[str],
            source_texts: List[str],
            batch_size: int = 32,
            rationality: int = 1,
            device="cuda",
    ):
        """
        :param model: hf model used to compute the likelihoods (supposed to be a seq2seq model), is S0 in the RSA model
        :param tokenizer:
        :param candidates: list of candidates summaries
        :param source_texts: list of source texts
        :param batch_size: batch size used to compute the likelihoods (can be high since we don't need gradients and
        it's a single forward pass)
        :param rationality: rationality parameter of the RSA model
        :param device: device used to compute the likelihoods
        """
        self.model = model
        self.device = device
        self.tokenizer = tokenizer

        self.candidates = candidates
        self.source_texts = source_texts

        self.batch_size = batch_size
        self.rationality = rationality

        self.model.to(self.device)

    def compute_conditionned_likelihood(
            self, x: List[str], y: List[str], mean: bool = True
    ) -> torch.Tensor:
        """
        Compute the likelihood of y given x

        :param x: list of source texts len(x) = batch_size
        :param y: list of candidates summaries len(y) = batch_size
        :param mean: average the likelihoods over the tokens of y or take the sum
        :return: tensor of shape (batch_size) containing the likelihoods of y given x
        """
        # Dummy inputs
        # source_texts = ["The paper is interesting."] -> 7 tokens
        # candidate_summaries = ["Well-written summary."] -> 7 tokens not necessary to have the same number of tokens
        assert len(x) == len(y)

        # Define the loss function (cross-entropy for token-level predictions)
        loss_fn = torch.nn.CrossEntropyLoss(reduction="none")

        if 'pegasus' in self.model.name_or_path:
          y = [summary for summary in y if isinstance(summary, str) and summary]
          x = x[:len(y)]  # Adjust x to match the filtered y length


        # Tokenize the source texts (x) and summaries (y)
        x = self.tokenizer(x, return_tensors="pt", padding=True, max_length=512,
                           truncation=True).to(self.device)
        y = self.tokenizer(y, return_tensors="pt", padding=True, max_length=512,
                           truncation=True).to(self.device)

        # Extract token IDs for input and output
        x_ids = x.input_ids.to(self.device)
        y_ids = y.input_ids.to(self.device)
        x_attention_mask = x.attention_mask.to(self.device)
        y_attention_mask = y.attention_mask.to(self.device)
        # print(x_ids.shape, y_ids.shape) -> (1, 7) (1, 7)
        # print(x_ids) -> tensor([[0,133,2225,16,2679,4,2]])

        # Pass the inputs through the model
        logits = self.model(
            input_ids=x_ids,
            decoder_input_ids=y_ids,
            attention_mask=x_attention_mask,
            decoder_attention_mask=y_attention_mask,
        ).logits

        # print(logits.shape) -> (1, 7, 50265)

        # Shift logits and token IDs for loss computation
        shifted_logits = logits[..., :-1, :].contiguous()
        shifted_ids = y_ids[..., 1:].contiguous()

        # print(shifted_logits.shape, shifted_ids.shape)
        # Result: (1, 6, 50265) (1, 6)

        # Compute token-level negative log-likelihood
        # shifted logits has a size (batch_size, sequence_length, vocab_size)
        # WE FLATTEN IT TO (batch_size x sequence_length, vocab_size)
        likelihood = -loss_fn(
            shifted_logits.view(-1, shifted_logits.size(-1)  # (1x6, 50265)
                                ), shifted_ids.view(-1)  # (1x6,)
        )

        # print(likelihood.shape) -> [6] == (6,)

        # Reshape the likelihood to match the batch
        # Reshape back to (batch_size, sequence_length) then sum(-1) -> (batch_size,)
        likelihood = likelihood.view(len(x["input_ids"]), -1).sum(-1)

        # print(likelihood.shape) -> [1] == (1,)

        # Normalize likelihood by the number of tokens if `mean=True`
        if mean:
            likelihood /= (y_ids !=
                           self.tokenizer.pad_token_id).float().sum(-1)

        # print(likelihood) = tensor([-6.6653])
        return likelihood

    def score(self, x: List[str], y: List[str], **kwargs):
        return self.compute_conditionned_likelihood(x, y, **kwargs)

    def likelihood_matrix(self) -> torch.Tensor:
        """
        Compute a likelihood matrix where entry (i, j) is the likelihood of
        candidate j summarizing source text i.

        Returns:
            torch.Tensor: Likelihood matrix of shape (len(source_texts), len(candidates)).
        """

        # initialize the likelihood matrix of size (len(source_texts), len(candidates))
        likelihood_matrix = torch.zeros(
            (len(self.source_texts), len(self.candidates))
        ).to(self.device)

        # create a list of pairs (i: index source, j: index candidate, source_text, candidate)
        pairs = []
        for i, source_text in enumerate(self.source_texts):
            for j, candidate in enumerate(self.candidates):
                pairs.append((i, j, source_text, candidate))

        batches = [
            pairs[i: i + self.batch_size]
            for i in range(0, len(pairs), self.batch_size)
        ]

        for batch in tqdm(batches):
            # get the source texts and candidates
            source_texts = [pair[2] for pair in batch]
            candidates = [pair[3] for pair in batch]

            # compute the likelihoods
            with torch.no_grad():
                likelihoods = self.score(
                    source_texts, candidates, mean=True
                )

            # fill the matrix
            # update the likelihood matrix with the likelihoods
            for k, (i, j, _, _) in enumerate(batch):
                likelihood_matrix[i, j] = likelihoods[k].detach()

        # return the likelihood matrix
        return likelihood_matrix


### Use ReRanker + Set of models to generate `pkl` files.

These generated files are nothing but the likelihood probabilties grouped by 'ID'.

The scripts iterators over models, for each it saves the computed likelihood probas in a well-defined pkl file

In [ ]:
model_for_likelihood_computation = {
    # 'model_1':
    #     {
    #         'model_id': "facebook/bart-large-cnn",
    #         'model_name': "BART"
    #     },
    # 'model_2':
    #     {
    #         'model_id': "Falconsai/text_summarization",
    #         'model_name': "Falcon"
    #     },
    # 'model_3':
    #     {
    #         'model_id': "google/pegasus-xsum",
    #         'model_name': "PEGASUS-XSUM"
    #     },
    # 'model_4':
    #     {
    #         'model_id': "google/bigbird-pegasus-large-arxiv",
    #         'model_name': "PEGASUS-BigBird-Arxiv"
    #     },
    # 'model_5':
    #     {
    #         'model_id': "google/pegasus-arxiv",
    #         'model_name': "PEGASUS-Arxiv"
    #     },
    # 'model_6':
    #     {
    #         'model_id': "google/pegasus-large",
    #         'model_name': "PEGASUS-Large"
    #     }

    # 'model_1':
    #     {
    #         'model_id': "pszemraj/led-base-book-summary",
    #         'model_name': "LED-Base"
    #     },
    # 'model_2':
    #     {
    #         'model_id': "pszemraj/led-large-book-summary",
    #         'model_name': "LED-Large"
    #     },
    # 'model_3':
    #     {
    #         'model_id': "mrm8488/flan-t5-large-finetuned-openai-summarize_from_feedback",
    #         'model_name': "FlanT5-Large-FT-OAI"
    #     },
    # 'model_4':
    #     {
    #         'model_id': "jordiclive/flan-t5-3b-summarizer",
    #         'model_name': "FlanT5-3BSUM"
    #     },
    # 'model_6':
    #     {
    #         'model_id': "lidiya/bart-large-xsum-samsum",
    #         'model_name': "BART-XSUM"
    #     },
    'model_7':
        {
            'model_id': "thepowerfuldeez/Qwen2-1.5B-Summarize",
            'model_name': "Qwen2"
        }

    }

path_candidates = Path("/content/drive/MyDrive/candidates2")

for model_count, model_info in model_for_likelihood_computation.items():
    # Load the model and tokenizer
    model_id = model_info['model_id']
    model_name = model_info['model_name']
    if "Qwen" in model_name:
      model = AutoModelForCausalLM.from_pretrained(model_id)
    else:
      model = AutoModelForSeq2SeqLM.from_pretrained(model_id)
    tokenizer = AutoTokenizer.from_pretrained(model_id)

    for file in path_candidates.glob('*.csv'):
        # For each dataset we want to do the following
        # Extract LM_probas for each dataframe
        # Save them in a pkl file for each 'paper' (id)
        # Save the pkl files in a folder named after the dataset and the model used

        results = []
        curr_ds = pd.read_csv(file)

        # Name is a tuple e.g. ('id_name',)
        # group is a GroupedByKey DataFrame

        for name, group in tqdm(curr_ds.groupby(["id"])):

            rsa_reranker = RSAReranking(
                model,  # model on which we want to compute the RSA
                tokenizer,  # tokenizer for the model
                device='cuda',
                candidates=group.summary.unique().tolist(),
                source_texts=group.text.unique().tolist(),
                batch_size=32,
                rationality=1,
            )
            # print(len(group.summary.unique().tolist()))
            # print(len(group.text.unique().tolist()))
            lm_probas = rsa_reranker.likelihood_matrix()
            # print(lm_probas.shape)
            lm_probas = lm_probas.cpu().numpy()
            lm_probas_df = pd.DataFrame(lm_probas)
            lm_probas_df.index = group.text.unique().tolist()
            lm_probas_df.columns = group.summary.unique().tolist()
            gold = group['gold'].tolist()[0]

            results.append(
                {
                    "id": name,
                    "language_model_proba_df": lm_probas_df,
                    "gold": gold,
                    "rationality": 1,  # hyperparameter
                    "text_candidates": group
                }
            )

        # Save the results
        opt_dir = Path(f'data/lm_probas/')
        if not opt_dir.exists():
            opt_dir.mkdir(parents=True, exist_ok=True)

        opt_path = Path(f"data/lm_probas/{file.stem}-_-{model_name}.pkl")
        results = {"results": results}
        with open(opt_path, 'wb') as f:
            pickle.dump(results, f)
    print(f'{file} is done')

print('ALL DONE :)')


OSError: Can't load tokenizer for 'thepowerfuldeez/Qwen2-1.5B-Summarize'. If you were trying to load it from 'https://huggingface.co/models', make sure you don't have a local directory with the same name. Otherwise, make sure 'thepowerfuldeez/Qwen2-1.5B-Summarize' is the correct path to a directory containing all relevant files for a Qwen2TokenizerFast tokenizer.

CELL USED FOR COMMIT 

In [ ]:
import os
from google.colab import auth
from google.colab import runtime

# Authenticate for access to Colab's secrets
auth.authenticate_user()
token = os.environ.get('github_tk')

if not token:
    raise ValueError("GitHub token not found in Colab Secrets.")

# Configure Git
repository_url = "https://github.com/alialhousseini/glimpse-mds.git"
tokenized_url = repository_url.replace("https://", f"https://{token}@")


# Make changes (if any), add, and commit
!git add -A
!git commit -m "Commit by colab!"

# Push changes
!git push origin main
# #############################

# import shutil

# # Define source and destination paths
# repo_path = "/content/glimpse-mds/data/lm_probas"  # Path to your data in the repository
# drive_path = "/content/drive/My Drive/lm_probas"

# # Check if the destination folder exists
# if not os.path.exists(drive_path):
#     os.makedirs(drive_path)  # Create the folder if it doesn't exist
#     print(f"Created folder: {drive_path}")

# # Copy the entire folder or specific files
# shutil.copytree(repo_path, drive_path)  # For folders
# # shutil.copy(f"{repo_path}/file.txt", drive_path)  # For individual files


ValueError: GitHub token not found in Colab Secrets.

Aggregator, it takes a set of models, and go to the folder, extract the corresponding `pkl` files. and apply the aggregation following the method providedd by the user. 

Returned results are also saved again in their appropriate format

In [ ]:

########################################################################

def elementwise_max(dfs):
    """
    dfs: list of DataFrames (same index/columns)
    """
    return reduce(lambda x, y: x.combine(y, func=max), dfs)

# Now we can write a script that takes the set of LM_probas for each dataset and (set) of models
# and aggregate them to get the final ranking

# We define a set of model names, this set represents the set of models we want to aggregate their results
# In addition we define a methodology of aggregation(e.g. mean, max, weighted_avg, etc.)

model_names = ["PEGASUS-Arxiv", "PEGASUS-BigBird-Arxiv", \
               "PEGASUS-Large", "PEGASUS-XSUM"]

# We need to find for each set of common datasets, the models we are looking for:
lm_probas_path = Path("/content/drive/MyDrive/lm_probas")
lm_probas_files = list(lm_probas_path.glob("*.pkl"))
# Filter out the files that do not contain the models we are looking for
# So we keep only the files that contain the models we are looking for
lm_probas_files = [file for file in lm_probas_files if any(
    model_name in file.stem.split('-_-')[-1] for model_name in model_names)]

# Now for each file, we collect filenames together to be processed
files_and_pickles = {}
for file in lm_probas_files:
    filename = file.stem.split('-_-')[0]
    if filename not in files_and_pickles:
        files_and_pickles[filename] = [file]
    else:
        files_and_pickles[filename].append(file)

method = "mean"

# Now we can aggregate the results
# We will aggregate the results for each dataset
for filename, files in tqdm(files_and_pickles.items(), desc="Processing datasets"):
    # We iterate over the dict
    # filename is the name of the dataset
    # files is a list of paths to the pkl files

    # Load the results for each model
    pkls = [pd.read_pickle(f) for f in files]
    # Go to results
    pkls = [f['results'] for f in pkls]
    # Now pkls is a list of lists of dictionaries [ [{},{},{}], [{},{},{}], ...]
    # We want to access the language_model_proba_df for each dictionary in parallel
    # i.e. [ [{a1},{b1},{c1}], [{a2},{b2},{c2}], ...] -> [ {a_i}, {b_i}, {c_i} ]

    # Results
    results = []
    for i in range(len(pkls[0])):  # iterate over the dictionaries
        # index 'i' is shared
        set_of_dicts = [pkls[j][i] for j in range(len(pkls))]
        # set_of_dicts is a list of dictionaries that share the same index
        # [{a1}, {a2}, {a3}, ...]
        # Now we want to aggregate the language_model_proba_df for each dictionary

        assert all(set_of_dicts[i]['id'] == set_of_dicts[0]['id'] for i in range(len(set_of_dicts))) , \
        f"Some IDs are not equal {set_of_dicts[i]['id']} != {set_of_dicts[0]['id']}"

        new_dict = {}
        new_dict['id'] = set_of_dicts[0]['id']
        new_dict['gold'] = set_of_dicts[0]['gold']
        new_dict['rationality'] = set_of_dicts[0]['rationality']
        new_dict['text_candidates'] = set_of_dicts[0]['text_candidates']
        # Now we want to aggregate the language_model_proba_df
        # THIS HAS TO BE DONE ACCORDING TO A METHOD (max, weighted_avg, etc.)
        set_of_dfs = [d['language_model_proba_df'] for d in set_of_dicts]

        # Additional check of consistency
        ref_index = set_of_dfs[0].index
        ref_columns = set_of_dfs[0].columns

        for t, df in enumerate(set_of_dfs[1:], start=2):
            # Compare sets OR compare ordered lists
            if not df.index.equals(ref_index):
                raise ValueError(
                    f"DataFrame #{i} index does not match the reference. "
                    f"Expected {list(ref_index)}, got {list(df.index)}."
                )
            if not df.columns.equals(ref_columns):
                raise ValueError(
                    f"DataFrame #{i} columns do not match the reference. "
                    f"Expected {list(ref_columns)}, got {list(df.columns)}."
                )

        # Combine data into a vector and save it in a new DF where each element
        # Is a list (vector)
        # Create a DataFrame where each cell is a list of integers
        df_concat = pd.DataFrame(
            [[list(row) for row in zip(*[df.iloc[i].values for df in set_of_dfs])]
              for i in range(set_of_dfs[0].shape[0])],
            index=ref_index,
            columns=ref_columns
        )

        # Save it
        new_dict['lm_probas_concat'] = df_concat

        if method == "mean":

            # To aggregation safely
            df_sum = reduce(operator.add, set_of_dfs)
            df_agg = df_sum / len(set_of_dfs)

        if method == "max":
            df_agg = elementwise_max(set_of_dfs)

        # Save it!
        new_dict['language_model_proba_df'] = df_agg

        # Save model names used as well
        new_dict['model_names'] = model_names

        results.append(new_dict)

    results = {"results": results}
    # Save the results
    ## CHANGE PATH BEFORE RUNNING

    opt_dir = Path(f'/content/drive/MyDrive/aggs_lm/')
    if not opt_dir.exists():
        opt_dir.mkdir(parents=True, exist_ok=True)
    str_list_model_names = "["+str("_".join(model_names))+"]"
    #e.g. all_merged_226_-_extr-_-[BART_PEGASUS-Arxiv_Falcon]-_-mean.pkl
    new_filename = filename + "-_-" + str_list_model_names + "-_-" + method

    ## CHANGE PATH BEFORE RUNNING
    opt_path = Path(f"/content/drive/MyDrive/aggs_lm/{new_filename}.pkl")
    with open(opt_path, 'wb') as f:
        pickle.dump(results, f)

print('ALL DONE :)')
########################################################################

Processing datasets:  25%|██▌       | 1/4 [00:00<00:02,  1.04it/s]

Results dumped!


Processing datasets:  50%|█████     | 2/4 [00:01<00:01,  1.04it/s]

Results dumped!


Processing datasets:  75%|███████▌  | 3/4 [00:02<00:00,  1.26it/s]

Results dumped!


Processing datasets: 100%|██████████| 4/4 [00:03<00:00,  1.04it/s]

Results dumped!
ALL DONE :)


#### SOME COMMANDS TO RUN AND GETTING RESULTS

In [ ]:
pwd

'/content/glimpse-mds'

In [ ]:
!python glimpse/evaluate/discriminative_classification.py --summaries_folder /content/drive/MyDrive/allSummariesGUnique/ --output_folder /content/drive/MyDrive/REPETITIONGLSUNIQUE/

python3: can't open file '/content/glimpse/evaluate/discriminative_classification.py': [Errno 2] No such file or directory


In [ ]:
!python glimpse/evaluate/discriminative_class_summy.py --summaries_folder /content/drive/MyDrive/summy --output_folder /content/drive/MyDrive/summy

2024-12-31 15:05:16.247274: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2024-12-31 15:05:16.265072: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-12-31 15:05:16.285616: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-12-31 15:05:16.291878: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-12-31 15:05:16.307108: I tensorflow/core/platform/cpu_feature_guar

In [ ]:
pwd

'/content/glimpse-mds'

In [ ]:
!python /content/glimpse-mds/glimpse/evaluate/evaluate_seahorse_metrics_samples.py --summaries_folder /content/drive/MyDrive/allSummariesGUnique --output_folder /content/drive/MyDrive/GLSUNIQUESEAHORSE/

Processing question: grammar with model google/seahorse-large-q3
config.json: 100% 884/884 [00:00<00:00, 6.37MB/s]
2025-01-10 14:21:46.731253: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-01-10 14:21:46.749038: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-01-10 14:21:46.770167: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-01-10 14:21:46.776526: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin 

In [ ]:
!zip -r /content/drive/MyDrive/GSpeakerRepetition.zip /content/drive/MyDrive/allSummariesGSpeakerRepetition
!zip -r /content/drive/MyDrive/GUniqueRepetition.zip /content/drive/MyDrive/REPETITIONGLSUNIQUE
!zip -r /content/drive/MyDrive/GLSUNIQUESEAHORSE.zip /content/drive/MyDrive/GLSUNIQUESEAHORSE


In [ ]:
from google.colab import files

files.download('/content/drive/MyDrive/GSpeakerRepetition.zip')
files.download('/content/drive/MyDrive/GUniqueRepetition.zip')
files.download('/content/drive/MyDrive/GLSUNIQUESEAHORSE.zip')

In [ ]:
%cd ..

/content


In [ ]:
!git clone https://github.com/maszhongming/UniEval.git

Cloning into 'UniEval'...
remote: Enumerating objects: 91, done.
remote: Counting objects: 100% (26/26), done.
remote: Compressing objects: 100% (21/21), done.
remote: Total 91 (delta 13), reused 5 (delta 5), pack-reused 65 (from 1)
Receiving objects: 100% (91/91), 1.97 MiB | 12.39 MiB/s, done.
Resolving deltas: 100% (22/22), done.


In [ ]:
%cd /content/UniEval/

/content/UniEval


In [ ]:
eval_scores

[{'coherence': 0.948185462558624,
  'consistency': 0.883035833838625,
  'fluency': 0.42928021353028545}]

The next cell is used to generate UNIEVAL metrics and add them as a new column for each dataset

In [ ]:
from utils import convert_to_json
from metric.evaluator import get_evaluator

task = 'summarization'

gspeaker_path = Path("/content/drive/MyDrive/allSummariesGSpeaker")
gunique_path = Path("/content/drive/MyDrive/allSummariesGUnique")
gsummy_path = Path("/content/drive/MyDrive/summy")


for path in [gspeaker_path, gunique_path, gsummy_path]:

  if path == gsummy_path:
    for file in tqdm(path.glob("*.csv")):
      df = pd.read_csv(file)
      summary_cols = [col for col in df.columns if "summary" in col]
      src_list = df.text.tolist()
      for col in summary_cols:
        output_list = df[col].values.tolist()
        model_name = col.split("_")[1]
        data = convert_to_json(output_list=output_list,
                       src_list=src_list)

        evaluator = get_evaluator(task)

        eval_scores = evaluator.evaluate(data, dims=['coherence', 'consistency', 'fluency'],
                                   overall=False, print_result=False)

        coherence = [eval_scores[i]['coherence'] for i in range(len(eval_scores))]
        consistency = [eval_scores[i]['consistency'] for i in range(len(eval_scores))]
        fluency = [eval_scores[i]['fluency'] for i in range(len(eval_scores))]

        df[f'coherence_{model_name}'] = coherence
        df[f'consistency_{model_name}'] = consistency
        df[f'fluency_{model_name}'] = fluency

      df.to_csv(file)

  else:
    for file in tqdm(path.glob("*.csv")):
      # open the file
      df = pd.read_csv(file)

      src_list = df.text.tolist()
      output_list = df.summary.tolist()

      data = convert_to_json(output_list=output_list,
                       src_list=src_list)

      evaluator = get_evaluator(task)

      eval_scores = evaluator.evaluate(data, dims=['coherence', 'consistency', 'fluency'],
                                 overall=False, print_result=False)

      coherence = [eval_scores[i]['coherence'] for i in range(len(eval_scores))]
      consistency = [eval_scores[i]['consistency'] for i in range(len(eval_scores))]
      fluency = [eval_scores[i]['fluency'] for i in range(len(eval_scores))]

      df['coherence'] = coherence
      df['consistency'] = consistency
      df['fluency'] = fluency

      df.to_csv(file)

0it [00:00, ?it/s]

Evaluating coherence of 226 samples !!!



100%|██████████| 29/29 [00:18<00:00,  1.53it/s]


Evaluating consistency of 226 samples !!!



100%|██████████| 59/59 [00:38<00:00,  1.51it/s]


...


100%|██████████| 30/30 [00:19<00:00,  1.50it/s]


Evaluating fluency of 226 samples !!!



100%|██████████| 30/30 [00:02<00:00, 11.93it/s]


Evaluating coherence of 226 samples !!!



 83%|████████▎ | 24/29 [00:16<00:03,  1.49it/s]

##### Computation (VECTORIZED DATA)

In [ ]:
from utils import convert_to_json
from metric.evaluator import get_evaluator

task = 'summarization'

gps_path = Path("/content/drive/MyDrive/vectorRSA_results")


for path in [gps_path ]:
    for file in tqdm(path.glob("*.csv")):
      # open the file
      df = pd.read_csv(file)
      if 'coherence' in df.columns:
        continue
      else:
        src_list = df.text.tolist()
        output_list = df.summary.tolist()

        data = convert_to_json(output_list=output_list,
                        src_list=src_list)

        evaluator = get_evaluator(task)

        eval_scores = evaluator.evaluate(data, dims=['coherence', 'consistency', 'fluency'],
                                  overall=False, print_result=False)

        coherence = [eval_scores[i]['coherence'] for i in range(len(eval_scores))]
        consistency = [eval_scores[i]['consistency'] for i in range(len(eval_scores))]
        fluency = [eval_scores[i]['fluency'] for i in range(len(eval_scores))]

        df['coherence'] = coherence
        df['consistency'] = consistency
        df['fluency'] = fluency

        df.to_csv(file)

16it [00:00, 43.27it/s]


In [ ]:
%%capture
!pip install rouge-score

In [ ]:
!python /content/glimpse-mds/glimpse/evaluate/evaluate_common_metrics_samples.py --summaries_folder /content/drive/MyDrive/vectorRSA_results --output_folder /content/drive/MyDrive/vectorRSA_results

Processing: 0it [00:00, ?it/s]Processing file: extr_vector_mean_GS.csv
Processing: 1it [00:09,  9.36s/it]Processing file: extr_vector_mean_GU.csv
Processing: 2it [00:17,  8.75s/it]Processing file: extr_vector_max_GS.csv
Processing: 3it [00:26,  8.67s/it]Processing file: extr_vector_max_GU.csv
Processing: 4it [00:34,  8.49s/it]Processing file: BART_vector_mean_GU.csv
Processing: 5it [00:49, 10.80s/it]Processing file: BART_vector_mean_GS.csv
Processing: 6it [01:06, 12.82s/it]Processing file: BART_vector_max_GS.csv
Processing: 7it [01:21, 13.61s/it]Processing file: BART_vector_max_GU.csv
Processing: 8it [01:36, 13.98s/it]Processing file: PEGASUS_Arxiv_vector_mean_GS.csv
Processing: 9it [02:19, 23.19s/it]Processing file: PEGASUS_Arxiv_vector_mean_GU.csv
Processing: 10it [02:59, 28.35s/it]Processing file: PEGASUS_Arxiv_vector_max_GS.csv
Processing: 11it [03:38, 31.57s/it]Processing file: PEGASUS_Arxiv_vector_max_GU.csv
Processing: 12it [04:17, 33.80s/it]Processing file: PEGASUS_Large_vector

In [ ]:
opt_path / Path(file.stem+'.csv')

PosixPath('/content/drive/MyDrive/TopModels/GSpeaker2/PEGASUS-Large_all_merged_226_-_abstr-_-[LED-Large_PEGASUS-Large_PEGASUS-BigBird-Arxiv]-_-mean_glimpseSpeaker.csv')

In [ ]:
# Loop to run the script multiple times

import os
import shutil
import subprocess
from sentence_transformers import SentenceTransformer
pth1 = Path('/content/drive/MyDrive/TopModels/GUnique')
opt_path = Path('/content/drive/MyDrive/TopModels/GUnique2')
if not opt_path.exists():
    opt_path.mkdir(parents=True, exist_ok=True)

!python /content/glimpse-mds/glimpse/evaluate/discriminative_classification.py --summaries_folder '/content/drive/MyDrive/TopModels/GSpeaker' --output_folder '/content/drive/MyDrive/TopModels/GSpeaker'

2025-01-11 18:15:46.407279: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-01-11 18:15:46.427980: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-01-11 18:15:46.434461: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-01-11 18:15:47.549851: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Could not find TensorRT
Processing files in /content/drive/MyDrive/TopModels/GSpeaker
0it [00:00, ?it/s]Processing file: all_merged_226_-_extr-_-[FlanT5-Large-FT-OAI_LED-Large_PEGASUS-BigBird-Arxiv]-_-mean_glimpseSpeaker.csv
Saved metrics to: /content/drive/MyDrive

In [ ]:
!python /content/glimpse-mds/glimpse/evaluate/discriminative_classification.py --summaries_folder "/content/drive/MyDrive/vectorRSA_results" --output_folder "/content/drive/MyDrive/vectorRSA_results"

2025-01-17 13:12:26.253653: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-01-17 13:12:26.272863: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-01-17 13:12:26.278664: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-01-17 13:12:26.292364: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-01-17 13:12:27.295551: W tensorflow/compiler/tf2

In [ ]:
%%capture
!pip install bert-score

In [ ]:
!python /content/glimpse-mds/glimpse/evaluate/evaluate_bartbert_metrics.py --summaries_folder /content/drive/MyDrive/vectorRSA_results --output_folder /content/drive/MyDrive/vectorRSA_results

tokenizer_config.json: 100% 25.0/25.0 [00:00<00:00, 243kB/s]
config.json: 100% 482/482 [00:00<00:00, 4.55MB/s]
vocab.json: 100% 899k/899k [00:00<00:00, 12.5MB/s]
merges.txt: 100% 456k/456k [00:00<00:00, 14.3MB/s]
tokenizer.json: 100% 1.36M/1.36M [00:00<00:00, 7.16MB/s]
2025-01-17 13:20:24.630857: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-01-17 13:20:24.650891: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-01-17 13:20:24.657016: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-01-17 13:20:24.671828: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlo